In [1]:
from google.colab import files

In [2]:
data = files.upload()
data

Saving valuable_customers(Busibud).csv to valuable_customers(Busibud).csv


In [5]:
data

**Importing Libraries**

In [3]:
import pandas as pd
import numpy as np
import warnings
warnings.filterwarnings('ignore')
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.cluster import KMeans
import plotly.express as px
import plotly.graph_objects as go

**Loading the Dataset**

In [9]:
df=pd.read_csv("valuable_customers(Busibud).csv", encoding= 'unicode_escape')
df.head()

InvoiceNo StockCode  ... CustomerID         Country
0    536365    85123A  ...    17850.0  United Kingdom
1    536365     71053  ...    17850.0  United Kingdom
2    536365    84406B  ...    17850.0  United Kingdom
3    536365    84029G  ...    17850.0  United Kingdom
4    536365    84029E  ...    17850.0  United Kingdom

[5 rows x 8 columns]

top 5 heads of the dataset.

In [10]:
df.tail()

InvoiceNo StockCode  ... CustomerID  Country
541904    581587     22613  ...    12680.0   France
541905    581587     22899  ...    12680.0   France
541906    581587     23254  ...    12680.0   France
541907    581587     23255  ...    12680.0   France
541908    581587     22138  ...    12680.0   France

[5 rows x 8 columns]

Bottom 5 of thhe dataset.

**Analysing the Patterns in the Dataset**

In [11]:
# Checking shape
df.shape

(541909, 8)

541909 rows and 8 columns in present in the dataset.

In [12]:
# Checking Datatype
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 541909 entries, 0 to 541908
Data columns (total 8 columns):
 #   Column       Non-Null Count   Dtype  
---  ------       --------------   -----  
 0   InvoiceNo    541909 non-null  object 
 1   StockCode    541909 non-null  object 
 2   Description  540455 non-null  object 
 3   Quantity     541909 non-null  int64  
 4   InvoiceDate  541909 non-null  object 
 5   UnitPrice    541909 non-null  float64
 6   CustomerID   406829 non-null  float64
 7   Country      541909 non-null  object 
dtypes: float64(2), int64(1), object(5)
memory usage: 33.1+ MB


2 float data type column, 1 integer data type column and 5 object data type columns are present in the dataset.

In [13]:
# Checking null values 
df.isnull().sum()

InvoiceNo           0
StockCode           0
Description      1454
Quantity            0
InvoiceDate         0
UnitPrice           0
CustomerID     135080
Country             0
dtype: int64

So null values are present in the dataset.

In [15]:
# Treating null values
df.dropna(axis=0,inplace=True)

In [16]:
# Treating null values
df.dropna(axis=0,inplace=True)

In [17]:
# Checking null values again
df.isnull().sum()

InvoiceNo      0
StockCode      0
Description    0
Quantity       0
InvoiceDate    0
UnitPrice      0
CustomerID     0
Country        0
dtype: int64

Null values are treated.

**Applying K-means Clustering for valuable customer segementationt**

In [18]:
kmeans_model = KMeans(init='k-means++',  max_iter=400, random_state=42)

model is defined and now we have to train.

**Training the model**

In [19]:
df.columns

Index(['InvoiceNo', 'StockCode', 'Description', 'Quantity', 'InvoiceDate',
       'UnitPrice', 'CustomerID', 'Country'],
      dtype='object')

In [20]:
kmeans_model.fit(df[['Quantity','CustomerID',
'UnitPrice']])

KMeans(max_iter=400, random_state=42)

Passing 3 features to fit method that is Quantity, Customer ID and UnitPrice.

 **Finding the number of clusters using elbow method**

In [21]:
# Create the K means model for different values of K
def try_different_clusters(K, data):
       
    cluster_values = list(range(1, K+1))
    inertias=[]
    
    for c in cluster_values:
        model = KMeans(n_clusters = c,init='k-means++',max_iter=400,random_state=42)
        model.fit(data)
        inertias.append(model.inertia_)
    
    return inertias

When we use the elbow method, we gradually increase the number of clusters from 2 until we reach the number of clusters where adding more clusters won’t cause a significant drop in the values of inertia.

In [22]:
# Find output for k values between 1 to 12 
outputs = try_different_clusters(12, df[['Quantity','CustomerID','UnitPrice']])
distances = pd.DataFrame({"clusters": list(range(1, 13)),"sum of squared distances": outputs})

we pass the values of K from 1 to 12 and calculate the inertia for each value of k.

In [23]:
# Finding optimal number of clusters k
figure = go.Figure()
figure.add_trace(go.Scatter(x=distances["clusters"], y=distances["sum of squared distances"]))

figure.update_layout(xaxis = dict(tick0 = 1,dtick = 1,tickmode = 'linear'),                  
                  xaxis_title="Number of clusters",
                  yaxis_title="Sum of squared distances",
                  title_text="Finding optimal number of clusters using elbow method")
figure.show()

The elbow of the code is at K=5. We have chosen 5 as if we increase the number of clusters to more than 5, there is very small change in the inertia.

In [24]:
# Re-Train K means model with k=5
kmeans_model_new = KMeans(n_clusters = 5,init='k-means++',max_iter=400,random_state=42)

kmeans_model_new.fit_predict(df[['Quantity','CustomerID','UnitPrice']])

array([0, 0, 0, ..., 4, 4, 4], dtype=int32)

Now we train the k-means clustering model again with the optimal number of clusters found.

**Now Visualizing the customer segement**

In [25]:
# Creating Data arrays
cluster_centers = kmeans_model_new.cluster_centers_
data = np.expm1(cluster_centers)
points = np.append(data, cluster_centers, axis=1)
points

array([[1.74496223e+05,            inf, 2.08656059e+01, 1.20696641e+01,
        1.77059981e+04, 3.08491490e+00],
       [3.80513258e+05,            inf, 2.54187568e+01, 1.28492789e+01,
        1.42495592e+04, 3.27407424e+00],
       [6.03774465e+04,            inf, 2.31216627e+01, 1.10083875e+01,
        1.65521368e+04, 3.18311030e+00],
       [3.46677733e+04,            inf, 4.54942605e+01, 1.04535947e+01,
        1.53243915e+04, 3.83932888e+00],
       [8.65374709e+05,            inf, 4.88440045e+01, 1.36709190e+01,
        1.29265381e+04, 3.90889822e+00]])

After this we will be able to tell which customer belongs to what cluster.

In [26]:
# Adding new column "clusters" to df
points = np.append(points, [[0], [1], [2], [3], [4]], axis=1)
df["clusters"] = kmeans_model_new.labels_

In [27]:
df.head(50)

InvoiceNo StockCode  ...         Country  clusters
0     536365    85123A  ...  United Kingdom         0
1     536365     71053  ...  United Kingdom         0
2     536365    84406B  ...  United Kingdom         0
3     536365    84029G  ...  United Kingdom         0
4     536365    84029E  ...  United Kingdom         0
5     536365     22752  ...  United Kingdom         0
6     536365     21730  ...  United Kingdom         0
7     536366     22633  ...  United Kingdom         0
8     536366     22632  ...  United Kingdom         0
9     536367     84879  ...  United Kingdom         4
10    536367     22745  ...  United Kingdom         4
11    536367     22748  ...  United Kingdom         4
12    536367     22749  ...  United Kingdom         4
13    536367     22310  ...  United Kingdom         4
14    536367     84969  ...  United Kingdom         4
15    536367     22623  ...  United Kingdom         4
16    536367     22622  ...  United Kingdom         4
17    536367     21754  ...  United Kingdom         4
18    536367     21755  ...  United Kingdom         4
19    536367     21777  ...  United Kingdom         4
20    536367     48187  ...  United Kingdom         4
21    536368     22960  ...  United Kingdom         4
22    536368     22913  ...  United Kingdom         4
23    536368     22912  ...  United Kingdom         4
24    536368     22914  ...  United Kingdom         4
25    536369     21756  ...  United Kingdom         4
26    536370     22728  ...          France         4
27    536370     22727  ...          France         4
28    536370     22726  ...          France         4
29    536370     21724  ...          France         4
30    536370     21883  ...          France         4
31    536370     10002  ...          France         4
32    536370     21791  ...          France         4
33    536370     21035  ...          France         4
34    536370     22326  ...          France         4
35    536370     22629  ...          France         4
36    536370     22659  ...          France         4
37    536370     22631  ...          France         4
38    536370     22661  ...          France         4
39    536370     21731  ...          France         4
40    536370     22900  ...          France         4
41    536370     21913  ...          France         4
42    536370     22540  ...          France         4
43    536370     22544  ...          France         4
44    536370     22492  ...          France         4
45    536370      POST  ...          France         4
46    536371     22086  ...  United Kingdom         1
47    536372     22632  ...  United Kingdom         0
48    536372     22633  ...  United Kingdom         0
49    536373    85123A  ...  United Kingdom         0

[50 rows x 9 columns]

After adding the new column, named clusters, the customer data dataset will look as above.

In [28]:
# Now visualizing the clusters that created

figure = px.scatter_3d(df,
                    color='clusters',
                    x="Quantity",
                    y="CustomerID",
                    z="UnitPrice",            
                    category_orders = {"clusters": ["0", "1", "2", "3", "4"]}                    
                    )
figure.update_layout()
figure.show()

**Conclusion**

Customers can have different needs and requirement ana customer segemntation helps the organization to serve better.
Finding an optimal number of unique customers group helps to understand the most valuable customers. Customer segmentation also helps to improve customer experience and boosts company revenue.